In [1]:
import xmltodict
from glob import glob
from tqdm import tqdm
from fastcore.xtras import save_pickle, load_pickle
import pandas as pd 
import re

In [2]:
example_xml = '/Users/kevinmaikjablonka/Downloads/grants/1976/pftaps19760113_wk02.xml'

In [3]:
with open(example_xml, 'r') as f:
    xml_dict = xmltodict.parse(f.read())

In [4]:
xml_dict

{'reactionList': {'@xmlns': 'http://www.xml-cml.org/schema',
  '@xmlns:cmlDict': 'http://www.xml-cml.org/dictionary/cml/',
  '@xmlns:nameDict': 'http://www.xml-cml.org/dictionary/cml/name/',
  '@xmlns:unit': 'http://www.xml-cml.org/unit/',
  '@xmlns:cml': 'http://www.xml-cml.org/schema',
  '@xmlns:dl': 'http://bitbucket.org/dan2097',
  'reaction': [{'dl:source': {'dl:documentId': 'US03932168',
     'dl:headingText': 'N-Cyanomethyl 2,4-Dichlorophenoxyacetamide',
     'dl:paragraphText': 'A solution of 11.95 g. (0.05 mole) of 2,4 dichlorophenoxyacetyl chloride in 50 ml. of benzene was added slowly to a stirred mixture of 10.1 g. (0.10 mole) of triethylamine and 4.2 g. (0.05 mole) aminoacetonitrile hydrochloride in 200 ml. of benzene. The mixture was stirred for 2 hours at room temperature and then washed successively with water, 5% sodium hydroxide solution, water, 5% hydrochloric acid solution, and water and then dried over magnesium sulfate. The resultant filtrate was concentrated unde

In [5]:
def has_product_yield(x):
    try:
        return any([y['@dl:propertyType']=='CALCULATEDPERCENTYIELD' for y in x['productList']['product']['amount']])
    except KeyError:
        return False
    except:
        return False

def has_product_amount(x):
    try:
        return any([y['@dl:propertyType']=='MASS' for y in x['productList']['product']['amount']])
    except KeyError:
        return False
    except:
        return False

def has_two_elements_in_product_list(x):
    try:
        return len(x['productList']['product'])==2
    except KeyError:
        return False
    except:
        return False

In [6]:
def get_reaction_list(xml_dict):
    return xml_dict['reactionList']['reaction']

In [7]:
reactions_with_yield = [x for x in get_reaction_list(xml_dict) if has_product_yield(x) and has_product_amount(x)]

In [8]:
reaction_w_yield = get_reaction_list(xml_dict)[-400]

In [9]:
has_product_yield(reaction_w_yield)

True

In [10]:
has_product_amount(reaction_w_yield)

True

In [11]:
len(reactions_with_yield)

59

It probably makes sense to remove the sentences with characterization data as they do not contain any information that we have *before* (or during) the reaction. At best, this only is superfluuos tokens. At worst, it is data leakage.

In [12]:
def remove_characterization_sentences(text): 
    sentences = re.split(r'\.\s+', text)
    sentences_without_characterization = []

    for sentence in sentences: 
        lower_sentence = sentence.lower()
        if ('NMR' and 'Hz') in sentence: # matching with the unicode delta gives weird results... 
            continue
        if ('MS' and 'm/z') in sentence:
            continue
        if ('recrystallization') in lower_sentence: # droping to be super safe, because sometimes mass is also here
            continue
        if ('m.p.' in lower_sentence) or ('melting point' in lower_sentence) or ('m. p.' in lower_sentence):
            continue
        if len(sentence.split()) < 3: # drop sentences that are too short
            continue
        sentences_without_characterization.append(sentence)
    return '. '.join(sentences_without_characterization)


In [13]:
def extract_data_from_reaction(reaction): 
    yield_amount = [x['@dl:normalizedValue'] for x in reaction['productList']['product']['amount'] if x['@dl:propertyType']=='CALCULATEDPERCENTYIELD'][0]
    mass_amount = [x['@dl:normalizedValue'] for x in reaction['productList']['product']['amount'] if x['@dl:propertyType']=='MASS'][0]
    
    # extract the yield text from the dl:reactionActionList
    yield_text = [x['dl:phraseText'] for x in reaction['dl:reactionActionList']['dl:reactionAction'] if x['@action']=='Yield'][0]

    reac_info = {
        'reaction_smiles': reaction['dl:reactionSmiles'],
        'yield': float(yield_amount),
        'mass': float(mass_amount),
        'yield_text': yield_text
    }
    reac_info.update(reaction['dl:source'])

    reac_info['paragraph_without_yield'] = reac_info['dl:paragraphText'].replace(reac_info['yield_text'], '').replace(' .', '.')
    reac_info['paragraph_without_yield_and_charac'] = remove_characterization_sentences(reac_info['paragraph_without_yield'])
    return reac_info

In [14]:
extract_data_from_reaction(reactions_with_yield[12])

{'reaction_smiles': '[O:1]1[CH2:3][CH:2]1[C:4]1[CH:8]=[C:7]([C:9]2[CH:14]=[CH:13][CH:12]=[CH:11][CH:10]=2)[O:6][N:5]=1.[OH:15][CH:16]1[CH2:21][CH2:20][NH:19][CH2:18][CH2:17]1>>[OH:1][CH:2]([C:4]1[CH:8]=[C:7]([C:9]2[CH:14]=[CH:13][CH:12]=[CH:11][CH:10]=2)[O:6][N:5]=1)[CH2:3][N:19]1[CH2:20][CH2:21][CH:16]([OH:15])[CH2:17][CH2:18]1',
 'yield': 50.4,
 'mass': 0.45,
 'yield_text': 'to give 3-[1-hydroxy-2-(4-hydroxypiperidino ) ethyl]-5-phenylisoxazole (450 mg)',
 'dl:documentId': 'US03932426',
 'dl:paragraphText': 'A mixture of 3-(1,2-epoxyethyl)-5-phenylisoxazole (580 mg) and 4-hydroxypiperidine (625 mg) is stirred for 0.5 hour at 80°C and then the mixture is subjected to a column chromatography using silica gel to give 3-[1-hydroxy-2-(4-hydroxypiperidino ) ethyl]-5-phenylisoxazole (450 mg). Recrystallization from ethyl acetate-hexane gives colorless prisms (259 mg). M. p. 117-119°C.',
 'paragraph_without_yield': 'A mixture of 3-(1,2-epoxyethyl)-5-phenylisoxazole (580 mg) and 4-hydroxypipe

In [15]:
all_xmls = glob('/Users/kevinmaikjablonka/Downloads/grants/*/*.xml')

In [16]:
len(all_xmls)

2460

In [ ]:
all_reactions = []

for xml in tqdm(all_xmls):
    with open(xml, 'r') as f:
        xml_dict = xmltodict.parse(f.read())
    try:
        reactions = get_reaction_list(xml_dict)
    except Exception as e:
        print(f'Error with {xml}: {e}')
    reactions_with_yield = [x for x in reactions if has_product_yield(x) and has_product_amount(x)]
    all_reactions.extend(reactions_with_yield)

In [ ]:
len(all_reactions)

This seems too little ...

In [18]:
save_pickle('all_reactions.pkl', all_reactions)

In [15]:
all_reactions = load_pickle('all_reactions.pkl')

In [16]:
all_reaction_data = []

for i, reaction in tqdm(enumerate(all_reactions)):
    try:
        all_reaction_data.append(extract_data_from_reaction(reaction))
    except Exception as e:
        print(f'Error with {i}')

2195it [00:00, 11086.35it/s]

Error with 151
Error with 529
Error with 534
Error with 556
Error with 1576
Error with 1577
Error with 1578
Error with 1579
Error with 1580
Error with 1581
Error with 1582
Error with 1584
Error with 1585
Error with 1587
Error with 1588
Error with 1593
Error with 1735
Error with 1736
Error with 1895
Error with 1896
Error with 1897
Error with 1898
Error with 1899
Error with 1900
Error with 1901
Error with 2014
Error with 2314
Error with 2467
Error with 2486
Error with 2555
Error with 2556
Error with 2557
Error with 2685
Error with 2686


4554it [00:00, 10435.69it/s]

Error with 3189
Error with 3190
Error with 3261
Error with 3535
Error with 3594
Error with 3609
Error with 3720
Error with 3866
Error with 4042
Error with 4280
Error with 4285
Error with 4286
Error with 4295
Error with 4296
Error with 4298
Error with 4627
Error with 5124
Error with 5125
Error with 5126
Error with 5127
Error with 5132
Error with 5133
Error with 5134
Error with 5135
Error with 5158
Error with 5163
Error with 5182
Error with 5191


7742it [00:00, 9709.75it/s] 

...

Error with 872148
Error with 872150
Error with 872191
Error with 872257
Error with 872265
Error with 872266
Error with 872635
Error with 872743
Error with 872744
Error with 872832
Error with 872940
Error with 872941
Error with 873029
Error with 873137
Error with 873138
Error with 873173
Error with 873174
Error with 873177
Error with 873268
Error with 873270
Error with 873271
Error with 873272
Error with 873275
Error with 873276
Error with 873277
Error with 873418
Error with 873515
Error with 873516
Error with 873538
Error with 873540
Error with 873541
Error with 873543
Error with 873544
Error with 873587
Error with 873588
Error with 873591
Error with 873592
Error with 873594
Error with 873596
Error with 873598
Error with 873600
Error with 873602
Error with 873640
Error with 873641
Error with 873644
Error with 873735
Error with 873737
Error with 873738
Error with 873739
Error with 873742
Error with 873743
Error with 873744
Error with 873885
Error with 873982
Error with 873983
Error with

878624it [01:20, 15603.71it/s]


Error with 875406
Error with 875407
Error with 875408
Error with 875409
Error with 875410
Error with 875411
Error with 875412
Error with 875413
Error with 875414
Error with 875415
Error with 875416
Error with 875417
Error with 875418
Error with 875419
Error with 875420
Error with 875421
Error with 875422
Error with 875424
Error with 875425
Error with 875426
Error with 875427
Error with 875428
Error with 875429
Error with 875430
Error with 875431
Error with 875432
Error with 875433
Error with 875434
Error with 875435
Error with 875436
Error with 875437
Error with 875493
Error with 875568
Error with 875570
Error with 875604
Error with 876097
Error with 876336
Error with 876339
Error with 876965
Error with 877204
Error with 877207
Error with 877526
Error with 877527
Error with 877529
Error with 877531
Error with 877532
Error with 877682
Error with 877685
Error with 877686
Error with 877687
Error with 877688
Error with 877692
Error with 877693
Error with 877694
Error with 877695
Error wit

882984it [01:20, 10916.04it/s]

Error with 878953
Error with 878963
Error with 879062
Error with 879082
Error with 879443
Error with 879444
Error with 879576
Error with 879577
Error with 879578
Error with 879580
Error with 879581
Error with 879582
Error with 879583
Error with 879584
Error with 879585
Error with 879587
Error with 879588
Error with 879589
Error with 879591
Error with 879593
Error with 879604
Error with 879605
Error with 879641
Error with 879642
Error with 879643
Error with 879644
Error with 879648
Error with 879649
Error with 879784
Error with 879785
Error with 879786
Error with 879787
Error with 879788
Error with 879789
Error with 879790
Error with 879791
Error with 879792
Error with 879793
Error with 879794
Error with 879800
Error with 879802
Error with 879803
Error with 879804
Error with 879805
Error with 879806
Error with 879807
Error with 879809
Error with 879810
Error with 879811
Error with 879812
Error with 879971
Error with 879972
Error with 879973
Error with 879975
Error with 879976
Error with

In [17]:
len(all_reaction_data)

855377

In [111]:
save_pickle('all_reaction_data.pkl', all_reaction_data)

In [114]:
df = pd.DataFrame(all_reaction_data)

In [116]:
df.iloc[1553]["paragraph_without_yield_and_charac"]

'The diol 26 (8.17 g, 78.44 mmol) in 12 ml dry toluene is initially introduced into a 50 ml round-bottomed flask equipped with an argon balloon flask and reflux condenser. The solution is stirred and sodium hydride (60% suspension in mineral oil) (1.53 g, 38.25 mmol) is added thereto in portions over a period of 45 min. The suspension is heated under reflux for 3 h under an argon blanketing gas atmosphere. 4-Methoxy-benzyl chloride (5.2 ml, 38.31 mmol) is then added over a period of 30 min and the mixture is boiled under reflux for 18 h. At the end of this period the reaction mixture is cooled to room temperature and poured into 50 ml water. The phases are separated and the aqueous phase is extracted with dichloromethane (3×50 ml). The combined organic phases are dried over Na2SO4 and concentrated under vacuum'

In [118]:
df.iloc[1553]["yield"]

40.0

In [117]:
df.to_csv('../data/USTPO_yields.csv', index=False)